MATHEMATICAL MODEL FOR ANTENNA RADIATION

Antenna radiation can be modeled using Maxwell's equations, antenna theory, and electromagnetic field analysis. 
The key aspects of antenna radiation include:

        Far-field radiation pattern

        Directivity and gain

        Radiation resistance and efficiency

        Polarization and impedance matching

1. BASIC ANTENNA PARAMETERS

Current Distribution and Radiated Fields
The radiation of an antenna is determined by its current distribution J(r').
The vector potential A(r) in the far field is:

       A(r) = (μ0 / 4π) ∫ J(r') (e^(-jkR) / R) dV'

    Where:

       R = |r − r'| is the distance from source to observation point

       k = 2π / λ is the wavenumber

      λ is the wavelength

      Far-Field Approximation (R >> λ)
      
    For r >> r', R ≈ r − r' · r̂, leading to:

      A(r) ≈ (μ0 e^(-jkr) / 4πr) ∫ J(r') e^(jkr' · r̂) dV'

The electric field E and magnetic field H in the far field are:

      E = −jω [A − (A · r̂) r̂]
      H = (1 / η) (r̂ × E)

      Where η = sqrt(μ0 / ε0) is the impedance of free space.


2. RADIATION PATTERN AND DIRECTIVITY
Radiated Power Density (Poynting Vector)

       The radiated power density is given by:

            S = (1 / 2) Re(E × H*)

       In spherical coordinates (r, θ, φ), the power pattern is:

            P(θ, φ) = r² |S(θ, φ)|

Directivity
          
        The directivity D(θ, φ) is:

             D(θ, φ) = [4π P(θ, φ)] / [∫₀²π ∫₀π P(θ, φ) sinθ dθ dφ]

       Peak directivity:
              D₀ = max[D(θ, φ)]

Antenna Gain

        The antenna gain G(θ, φ) relates to directivity and radiation efficiency er:

             G(θ, φ) = er D(θ, φ)

             Where 0 ≤ er ≤ 1.

3. EXAMPLE: DIPOLE ANTENNA

       Short Dipole (Hertzian Dipole)
             Current distribution: I(z') = I₀ δ(z')

       Far-field electric field:
              Eθ = jη (I₀ℓ / 2λr) e^(-jkr) sinθ

        Radiation pattern:
             P(θ) ∝ sin²θ (doughnut-shaped)

       Directivity:
              D₀ = 1.5 (1.76 dBi)

             Half-Wave Dipole (ℓ = λ / 2)
             Current distribution: I(z') = I₀ cos(kz')

       Far-field electric field:
             Eθ = jη (I₀ / 2πr) e^(-jkr) [cos(π/2 cosθ) sinθ]

       Directivity:
              D₀ ≈ 2.15 (3.14 dBi)

4. ANTENNA IMPEDANCE AND EFFICIENCY
Radiation Resistance


       The radiation resistance Rr is:

            Rr = 2Prad / |I₀|²

       For a short dipole:

            Rr = 80π² (ℓ / λ)²

       Total Efficiency

             er = Rr / (Rr + Rloss)

             Where Rloss represents ohmic and ground losses.


5. ARRAY ANTENNAS (PHASED ARRAYS)


        For an array of N elements, the array factor AF is:

               AF(θ, φ) = Σ (n = 1 to N) In e^(jkrn · r̂)

        The total radiation pattern is:

                Ptotal(θ, φ) = Pelement(θ, φ) |AF(θ, φ)|²

In [1]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from mpl_toolkits.mplot3d import Axes3D
from IPython.display import HTML
%matplotlib inline

# ANTENNA VISUALIZATION

# Initialize figure
fig = plt.figure(figsize=(10, 8))
ax = fig.add_subplot(111, projection='3d')

# Antenna parameters
params = {
    'type': 'dipole',  # 'dipole' or 'array'
    'dipole_range': (0.1, 2.0),  # Length range (λ)
    'array_elements': 4,  # Number of elements
    'array_spacing': 0.5,  # Element spacing (λ)
    'resolution': 90  # Angular resolution
}

def dipole_pattern(theta, length):
    """Calculate dipole radiation pattern"""
    if length < 0.01:  # Short dipole approximation
        return np.abs(np.sin(theta))
    k = 2 * np.pi
    beta = k * length
    num = np.cos(beta * np.cos(theta)) - np.cos(beta)
    den = np.sin(theta)
    with np.errstate(divide='ignore', invalid='ignore'):
        pattern = np.abs(num / den)
        pattern[np.isnan(pattern)] = 0  # Handle division by zero
    return pattern

def array_factor(theta, N, spacing, phase):
    """Calculate array factor"""
    psi = 2 * np.pi * spacing * np.cos(theta) + phase
    if N == 1:
        return 1
    with np.errstate(divide='ignore', invalid='ignore'):
        af = np.abs(np.sin(N * psi / 2) / np.sin(psi / 2))
        af[np.isnan(af)] = N  # Handle division by zero
    return af

def update(frame):
    """Animation update function"""
    ax.clear()
    
    # Generate grid
    theta = np.linspace(0, np.pi, params['resolution'])
    phi = np.linspace(0, 2*np.pi, params['resolution'])
    Theta, Phi = np.meshgrid(theta, phi)
    
    if params['type'] == 'dipole':
        # Vary dipole length
        length = params['dipole_range'][0] + (frame/30) * (params['dipole_range'][1] - params['dipole_range'][0])
        E = dipole_pattern(Theta, length)
        title = f"Dipole Antenna (Length = {length:.2f}λ)"
    else:
        # Vary array phase
        phase = (frame/30) * 2*np.pi
        E = array_factor(Theta, params['array_elements'], params['array_spacing'], phase)
        title = f"{params['array_elements']}-Element Array (Phase Δ = {phase:.2f} rad)"
    
    # Convert to 3D coordinates
    X = E * np.sin(Theta) * np.cos(Phi)
    Y = E * np.sin(Theta) * np.sin(Phi)
    Z = E * np.cos(Theta)
    
    # Normalize and plot
    max_E = np.max(E)
    if max_E > 0:
        X, Y, Z = X/max_E, Y/max_E, Z/max_E
    
    ax.plot_surface(X, Y, Z, cmap='plasma', alpha=0.8)
    ax.set_title(title, pad=20)
    ax.set_xlim(-1, 1)
    ax.set_ylim(-1, 1)
    ax.set_zlim(-1, 1)
    ax.grid(False)

# Create animation
ani = FuncAnimation(fig, update, frames=30, interval=100, blit=False)

# Display in notebook
plt.close()  # Prevents duplicate display
HTML(ani.to_jshtml())